# Import / Config

In [ ]:
import pandas as pd
from sqlalchemy import create_engine
from neo4j import GraphDatabase

## Postgres

In [ ]:
userid = 'uuu'
password= 'ppp'
host = 'hhh'
db = 'adbkt'

url = f"postgresql://{userid}:{password}@{host}/{db}"
engine = create_engine(url, pool_size=1, max_overflow=0)

In [ ]:
pg_con = engine.connect()

In [ ]:
pg_con.close()
engine.dispose()

In [ ]:
sql = "select * from umobility.haltestelle"
haltestellen_pdf = pd.read_sql_query(sql, pg_con)

In [ ]:
haltestellen_pdf

## neo4j

In [ ]:
neo4j_uri = "neo4j://localhost:7687"

In [ ]:
cypher_create_stop = 'CREATE (h:Haltestelle {hid: $hid, bez: $bez, lat:$lat, lng:$lng})'
with GraphDatabase.driver(neo4j_uri, auth=("neo4j", "neo4j")) as driver:
    with driver.session() as session:
        for r in haltestellen_pdf.itertuples(index=False):
            session.run(cypher_create_stop, hid=r.hid, bez=r.bez, lat=r.lat, lng=r.lng)

In [ ]:
cypher_read_stops = 'MATCH (h:Haltestelle) return h.hid as hid, h.bez as bez'
with GraphDatabase.driver(neo4j_uri, auth=("neo4j", "neo4j")) as driver:
    with driver.session() as session:
        result = session.run(cypher_read_stops)
        haltestellen_neo4j_pdf = pd.DataFrame(result.data())


In [ ]:
haltestellen_neo4j_pdf